In [1]:
import sys
sys.path.insert(0, '/Users/acheung/TC_RI_P1/scripts/Useful Functions/')
import pandas as pd
import datetime as dt
import os
import h5py
import numpy as np
import matplotlib.pyplot as plt
import xarray as xr
from scipy import ndimage
from distance import distance_calculator
from cylindrical_conversion import interp_to_equal_grid,circle,x_y_grid_to_cylindrical
from mpl_toolkits.axes_grid1.inset_locator import inset_axes
from misc_useful_funcs import multiple_conditions_index_finder

In [2]:
# Select storms before downloading IMERG
# IMERG BEGINS HERE (Filter out anything before)
begin_imerg_YEAR = 2000
begin_imerg_DAY_OF_YEAR = 153
imerg_begin_date = dt.datetime(begin_imerg_YEAR, 1, 1) + dt.timedelta(begin_imerg_DAY_OF_YEAR - 1)

# Open both basin's SHIPS files
SHIPS_NATL = pd.read_csv('/Users/acheung/data/SHIPS/all_SHIPs_data_combined_north_atlantic.csv')
SHIPS_NATL = SHIPS_NATL.where(pd.to_datetime(SHIPS_NATL['Time']) >= imerg_begin_date).dropna()
SHIPS_EPAC = pd.read_csv('/Users/acheung/data/SHIPS/all_SHIPs_data_combined_east_pacific.csv')
SHIPS_EPAC = SHIPS_EPAC.where(pd.to_datetime(SHIPS_EPAC['Time']) >= imerg_begin_date).dropna()
# Reindex EPAC/CPAC to be after NATL
SHIPS_EPAC.index = np.arange(len(SHIPS_NATL),len(SHIPS_NATL) + len(SHIPS_EPAC))

SHIPS = pd.concat([SHIPS_NATL,SHIPS_EPAC])
# Select only tropical storms
tropical_inds = SHIPS.where(SHIPS['TYPE'] == 1).dropna().index

# Select storms at least 50 km from land

dtl_inds = SHIPS.where(SHIPS['DTL'] >=50).dropna().index

# Select Storm with at least 10 KJ/cm2 OHC

ohc_inds =  SHIPS.where(SHIPS['COHC'] >=10).dropna().index

# Select Storm with at least 40% Mid-level (700–500 hPa) RH

rhmd_inds =  SHIPS.where(SHIPS['RHMD'] >=40).dropna().index

result = multiple_conditions_index_finder([tropical_inds,dtl_inds,ohc_inds,rhmd_inds])

# Cases that meet all criteria set above
filtered_cases = SHIPS.iloc[result]

In [ ]:
# Download IMERG Data
timedeltas = [-60,-30,0,30] # zero is 0 to 30 minutes and thirty is 30 mins to 1 h
# timedeltas = [0] # zero is 0 to 30 minutes and thirty is 30 mins to 1 h

filepaths = []
desired_time_list = []
for i in filtered_cases.index:
    curr_time_filepaths = []
    for times in timedeltas:
        current_dt_obj = dt.datetime.strptime(filtered_cases['Time'][i],'%Y-%m-%d %H:%M:%S')
        time_desired = current_dt_obj + dt.timedelta(minutes=times)
#         print(i,current_dt_obj,time_desired)

        year = time_desired.year
        day_of_year = time_desired.strftime('%j')
        day_stripped = time_desired.strftime('%Y%m%d')
        time_stripped = time_desired.strftime('%H%M%S')
        min_of_day = str(time_desired.hour*60 + time_desired.minute).zfill(4)
        end_time_stripped = (time_desired+dt.timedelta(minutes=29,seconds=59)).strftime('%H%M%S')

        # If IMERG file does not exist, download it
        IMERG_file_path = '/Users/acheung/data/IMERG/'+str(year)+'/'+day_of_year+'/'+\
            '3B-HHR.MS.MRG.3IMERG.'+day_stripped+'-S'+time_stripped+'-E'+end_time_stripped+\
            '.'+min_of_day+'.V07B.HDF5'
        curr_time_filepaths.append(IMERG_file_path)
        # print(IMERG_file_path)
        # print(os.path.exists(IMERG_file_path))

            # If day directory does not exist, make day directory
        if os.path.exists('/Users/acheung/data/IMERG/'+str(year)) == False:
            os.mkdir('/Users/acheung/data/IMERG/'+str(year))

        if os.path.exists('/Users/acheung/data/IMERG/'+str(year)+'/'+day_of_year) == False:
            os.mkdir('/Users/acheung/data/IMERG/'+str(year)+'/'+day_of_year)

        if os.path.exists(IMERG_file_path) == False:
            url_desired = "https://gpm1.gesdisc.eosdis.nasa.gov/data/GPM_L3/GPM_3IMERGHH.07/"\
                +str(year)+'/'+day_of_year+'/'+'3B-HHR.MS.MRG.3IMERG.'+day_stripped+'-S'+time_stripped+\
                '-E'+end_time_stripped+'.'+min_of_day+'.V07B.HDF5'
            os.chdir('/Users/acheung/data/IMERG/'+str(year)+'/'+day_of_year)

            os.system('wget --load-cookies ~/.urs_cookies --save-cookies ~/.urs_cookies --keep-session-cookies '
                      + url_desired)
    filepaths.append(curr_time_filepaths)
    desired_time_list.append(current_dt_obj)

all_time_filepaths = pd.DataFrame(filepaths)
all_time_filepaths.index = filtered_cases.index

case_loop_list = []
all_last_slices = []
progress = 1
for case_loop in all_time_filepaths.index.values: # Run all
# for case_loop in [8686]: # Run all

    # Open IMERG
    print('Index: '+str(case_loop)+'; In Progress: '+str(progress) + ' of ' 
          + str(len(all_time_filepaths.index.values)))
    precip_list = []
    for now_it in range(len(all_time_filepaths.loc[case_loop])):
        fn = all_time_filepaths.loc[case_loop][now_it]
        try:
            f = h5py.File(fn, 'r')
        except: # If the file is corrupt, remove and re-download
            os.system('rm ' + fn)
            os.chdir(fn[0:35])
            new_url = 'https://gpm1.gesdisc.eosdis.nasa.gov/data/GPM_L3/GPM_3IMERGHH.07/' + fn[26:]
            os.system('wget --load-cookies ~/.urs_cookies --save-cookies ~/.urs_cookies --keep-session-cookies '
                      + new_url)
            f = h5py.File(fn, 'r')


        # Work on precip file
        groups = [ x for x in f.keys() ]
        # print(groups)
        gridMembers = [ x for x in f['Grid'] ]
        # print(gridMembers)

        # Get the precipitation, latitude, and longitude variables
        precip = f['Grid/precipitation'][0][:][:]
        precip = np.transpose(precip)
        precip[precip<-999]=np.nan

        theLats = f['Grid/lat'][:]
        theLons = f['Grid/lon'][:]
        x, y = np.float32(np.meshgrid(theLons, theLats))

        precip_list.append(precip)

    # For now, we take a mean. Might need a different filter in the future
    precip_mean = np.mean(np.asarray(precip_list),axis=0)
    
    centering_lat = filtered_cases.loc[case_loop]['LAT']
    centering_lon = filtered_cases.loc[case_loop]['LON'] # Degrees W
    if centering_lon < 180: # Adjust lon from degrees W to -180 to 180
        centering_lon = centering_lon * -1
    elif centering_lon >= 180:
        centering_lon = centering_lon + 360
    
    distance_arr = distance_calculator(x, y,(centering_lon,centering_lat))

    abs_dist_arr = (abs(distance_arr))

    min_dist_ind = np.where(abs_dist_arr == np.nanmin(abs_dist_arr))
    
    # Slice arrays to within 100 indices of interpolated best-track center

    sliced_lon_grid = x[min_dist_ind[0][0]-100:min_dist_ind[0][0]+100,min_dist_ind[1][0]-100:min_dist_ind[1][0]+100]

    sliced_lat_grid = y[min_dist_ind[0][0]-100:min_dist_ind[0][0]+100,min_dist_ind[1][0]-100:min_dist_ind[1][0]+100]

    sliced_precip = precip_mean[min_dist_ind[0][0]-100:min_dist_ind[0][0]+100,min_dist_ind[1][0]-100:min_dist_ind[1][0]+100]

    # NEVER FORGET TO MULTIPLY RADIUS ARRAYS BY DX FOR IMERG PLOTS!!!

    dx = 2
    dy = 2

    # Interpolate IMERG data to equal-distance grid

    eq_lon_grid,eq_lat_grid,eq_dist_data = interp_to_equal_grid(sliced_lon_grid,sliced_lat_grid,
                                                            sliced_precip,dx = dx,dy=dy)
    
    
    distance_arr_sliced = distance_calculator(eq_lon_grid, eq_lat_grid,(centering_lon,centering_lat))

    abs_dist_arr_sliced = (abs(distance_arr_sliced))

    min_dist_ind_sliced = np.where(abs_dist_arr_sliced == np.nanmin(abs_dist_arr_sliced))

    pts_above = eq_dist_data.shape[0] - min_dist_ind_sliced[0][0]
    y_range = np.arange(-min_dist_ind_sliced[0][0],pts_above) * dy

    pts_right = eq_dist_data.shape[1] - min_dist_ind_sliced[1][0]
    x_range = np.arange(-min_dist_ind_sliced[1][0],pts_right) * dx

    xv, yv = np.meshgrid(x_range, y_range)

    x_range.shape[0],np.where(x_range==0)[0][0]

    x_zero_loc = np.where(x_range==0)[0][0]

    if x_zero_loc > x_range.shape[0]/2:
        x_offset = int(x_range.shape[0]-x_zero_loc)
    elif x_zero_loc <= x_range.shape[0]/2:
        x_offset = x_zero_loc

    y_zero_loc = np.where(y_range==0)[0][0]

    if y_zero_loc > y_range.shape[0]/2:
        y_offset = int(y_range.shape[0]-y_zero_loc)
    elif y_zero_loc <= y_range.shape[0]/2:
        y_offset = y_zero_loc

    x_even_inds = x_range[x_zero_loc-(x_offset-1):x_zero_loc+x_offset+1]
    y_even_inds = y_range[y_zero_loc-(y_offset-1):y_zero_loc+y_offset+1]

    sliced_eq_data_pd = pd.DataFrame(eq_dist_data,columns=x_range,index=y_range)

    evenly_sliced_pd = sliced_eq_data_pd[x_even_inds].loc[y_even_inds]

    x_evenly_sliced, y_evenly_sliced = np.meshgrid(x_even_inds, y_even_inds)
    
    angle_rotate = 90 - filtered_cases.loc[case_loop]['SHTD'] # Convert to math angle for rotation
    
    img_rotate = ndimage.rotate(evenly_sliced_pd, angle_rotate, reshape=False,cval=np.nan)
    img_rotate_pd = pd.DataFrame(img_rotate,columns=evenly_sliced_pd.columns,index=evenly_sliced_pd.index)

    pd_last_slice = img_rotate_pd[np.arange(-300,300.1,dx)].loc[-300:300]
    x_evenly_last_sliced, y_evenly_last_sliced = np.meshgrid(pd_last_slice.columns, pd_last_slice.index)
    
    # Save rotated and sliced data to list
    all_last_slices.append(pd_last_slice)

#     # Convert to polar grid
#     cylindrical_data, THETA, rad_arr = x_y_grid_to_cylindrical(
#         center_inds=[0,0],radius_min=0,radius_max=500,radius_interval=1, NOP=1000,
#         x_grid=img_rotate_pd.index.values,y_grid=img_rotate_pd.columns.values,
#         data=img_rotate_pd.values)
    
#     rmw_now = 

#     # Interpolate data to normalized RMW spacings
#     normalized_rad_arr = rad_arr/rmw_now

#     polar_interp = RegularGridInterpolator((normalized_rad_arr,THETA), cylindrical_data,bounds_error=False)

#     theta_mesh,desired_rad_mesh = np.meshgrid(THETA,desired_normalized_rad_arr)
#     polar_rad_norm_data = polar_interp((desired_rad_mesh,THETA))            

#     cylindrical_normalized_list.append(polar_rad_norm_data)
        
    case_loop_list.append(case_loop) 
    progress = progress + 1

finalx,finaly = np.meshgrid(pd_last_slice.columns,pd_last_slice.index)

# NEED TO FIX DATAFRAME INDEX HERE!!! 


finalx,finaly = np.meshgrid(pd_last_slice.columns,pd_last_slice.index)

all_last_slices_xr = xr.DataArray(all_last_slices,dims=["case","x", "y"],coords=dict(
        x=(["x", "y"], finalx),
        y=(["x", "y"], finaly),
        case=(case_loop_list)
    ))

all_last_slices_xr.to_netcdf('/Users/acheung/data/Composite_Data/imerg_NATL_EPAC_WPAC_composites.nc')

--2024-08-16 12:17:45--  https://gpm1.gesdisc.eosdis.nasa.gov/data/GPM_L3/GPM_3IMERGHH.07/2000/268/3B-HHR.MS.MRG.3IMERG.20000924-S110000-E112959.0660.V07B.HDF5
Resolving gpm1.gesdisc.eosdis.nasa.gov (gpm1.gesdisc.eosdis.nasa.gov)... 198.118.197.50, 2001:4d0:241a:4041::50
Connecting to gpm1.gesdisc.eosdis.nasa.gov (gpm1.gesdisc.eosdis.nasa.gov)|198.118.197.50|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 7489510 (7.1M) [application/x-troff-ms]
Saving to: ‘3B-HHR.MS.MRG.3IMERG.20000924-S110000-E112959.0660.V07B.HDF5’

     0K .......... .......... .......... .......... ..........  0% 9.81M 1s
    50K .......... .......... .......... .......... ..........  1% 10.7M 1s
   100K .......... .......... .......... .......... ..........  2% 18.5M 1s
   150K .......... .......... .......... .......... ..........  2% 10.3M 1s
   200K .......... .......... .......... .......... ..........  3% 19.7M 1s
   250K .......... .......... .......... .......... ..........  4% 19.

Index: 0; In Progress: 1 of 10951
Index: 1; In Progress: 2 of 10951
Index: 2; In Progress: 3 of 10951
Index: 3; In Progress: 4 of 10951
Index: 4; In Progress: 5 of 10951
Index: 5; In Progress: 6 of 10951
Index: 6; In Progress: 7 of 10951
Index: 7; In Progress: 8 of 10951
Index: 8; In Progress: 9 of 10951
Index: 9; In Progress: 10 of 10951
Index: 10; In Progress: 11 of 10951
Index: 11; In Progress: 12 of 10951
Index: 12; In Progress: 13 of 10951
Index: 13; In Progress: 14 of 10951
Index: 14; In Progress: 15 of 10951
Index: 15; In Progress: 16 of 10951
Index: 16; In Progress: 17 of 10951
Index: 17; In Progress: 18 of 10951
Index: 18; In Progress: 19 of 10951
Index: 19; In Progress: 20 of 10951
Index: 20; In Progress: 21 of 10951
Index: 21; In Progress: 22 of 10951
Index: 22; In Progress: 23 of 10951
Index: 23; In Progress: 24 of 10951
Index: 27; In Progress: 25 of 10951
Index: 29; In Progress: 26 of 10951
Index: 33; In Progress: 27 of 10951
Index: 34; In Progress: 28 of 10951
Index: 35; 

In [ ]:
filtered_cases['Time'] = pd.to_datetime(filtered_cases['Time'])

In [ ]:
imerg_cases = xr.open_dataset('/Users/acheung/data/Composite_Data/imerg_NATL_EPAC_WPAC_composites.nc')['__xarray_dataarray_variable__']

In [ ]:
# Identify times with 20 kt/12 h increases

boo_list = []
for f_i in filtered_cases.index:
    current_storm_time = filtered_cases.loc[f_i]
    current_vmax = filtered_cases['VMAX'].where(filtered_cases['Storm_ID'] == current_storm_time['Storm_ID']).dropna()
    
    # Check to see intensity 12 h later exists, if so, then calculate difference
    if sum(current_vmax.index.isin([current_storm_time.name + 2])) == 0: # No value 12 h later
        ri_boo = 0
    else: # Has value 12 h later, check RI or not
        intensity_12_h_change = current_vmax[current_storm_time.name + 2] - current_vmax[current_storm_time.name]
        if intensity_12_h_change >= 20: # 20 or greater
            ri_boo = 1
        else:
            ri_boo = 0
        
        if (intensity_12_h_change < 20) & (intensity_12_h_change > 5): # 10, 15
            slowly_boo = 1
        else:
            slowly_boo = 0
        
        if (intensity_12_h_change >= -5) & (intensity_12_h_change <=5): # -5, 0, 5
            ss_boo = 1
        else:
            ss_boo = 0
        
        if intensity_12_h_change <-5: # less than -5
            weakening_boo = 1
        else:
            weakening_boo = 0
            
            
    boo_list.append([ri_boo,slowly_boo,ss_boo,weakening_boo])
    
boolean_pd = pd.DataFrame(boo_list,index=filtered_cases.index,columns=['RI Boolean','Slowly-Intensifying Boolean',
                                                                  'Steady-State Boolean','Weakening Boolean'])

filtered_with_boo = pd.concat([filtered_cases,boolean_pd],axis=1)
filtered_with_boo_multi_index = filtered_with_boo.set_index(['Time','Storm_ID','Name'], append=True)


In [ ]:
# Weak indices
weak_storm_indices = filtered_cases.where((filtered_cases['VMAX'] <= 65) & (filtered_cases['VMAX'] > 0)).dropna().index

# Shear indices
weak_shear_indices = filtered_cases.where(filtered_cases['SHRD'] < 10).dropna().index
moderate_shear_indices = filtered_cases.where((filtered_cases['SHRD'] >= 10) & (filtered_cases['SHRD'] < 20)).dropna().index
strong_shear_indices = filtered_cases.where(filtered_cases['SHRD'] >= 20).dropna().index

# RI Indices
RI_indices = filtered_with_boo.where(filtered_with_boo['RI Boolean'] == 1).dropna().index
Non_RI_indices = filtered_with_boo.where(filtered_with_boo['RI Boolean'] == 0).dropna().index

# Slowly-Intensifying Indices
Slowly_intensifying_indices = filtered_with_boo.where(filtered_with_boo['Slowly-Intensifying Boolean'] == 1).dropna().index
Non_Slowly_intensifying_indices = filtered_with_boo.where(filtered_with_boo['Slowly-Intensifying Boolean'] == 0).dropna().index

# Steady-State Indices
SS_indices = filtered_with_boo.where(filtered_with_boo['Steady-State Boolean'] == 1).dropna().index
Non_SS_indices = filtered_with_boo.where(filtered_with_boo['Steady-State Boolean'] == 0).dropna().index

# Weakening Indices
Weakening_indices = filtered_with_boo.where(filtered_with_boo['Weakening Boolean'] == 1).dropna().index
Non_Weakening_indices = filtered_with_boo.where(filtered_with_boo['Weakening Boolean'] == 0).dropna().index


In [ ]:
weak_storm_and_weak_shear_imerg = imerg_cases.sel(case=multiple_conditions_index_finder([weak_storm_indices,weak_shear_indices]))
weak_storm_and_moderate_shear_imerg = imerg_cases.sel(case=multiple_conditions_index_finder([weak_storm_indices,moderate_shear_indices]))
weak_storm_and_strong_shear_imerg = imerg_cases.sel(case=multiple_conditions_index_finder([weak_storm_indices,strong_shear_indices]))


fig = plt.figure(figsize=(20, 7)) 

gs = fig.add_gridspec(1,3)
ax = fig.add_subplot(gs[0, 0],adjustable='box', aspect=1)
ax2 = fig.add_subplot(gs[0, 1],adjustable='box', aspect=1)
ax3 = fig.add_subplot(gs[0, 2],adjustable='box', aspect=1)

small_shear_cf = ax.contourf(imerg_cases['x'], imerg_cases['y'],weak_storm_and_weak_shear_imerg.mean('case'),
                              levels=np.arange(0,7.1,0.5),cmap='jet')
ax.grid()
ax.set_title('IMERG Weak-Shear (< 10 kt) \n n = ' + str(len(weak_storm_and_weak_shear_imerg)))
ax.set_xlabel('Along-Shear Direction (km)')
ax.set_ylabel('Across-Shear Direction (km)')

axins = inset_axes(ax, width="25%", height="9%", loc=3, borderpad=0)
axins.tick_params(labelleft=False, labelbottom=False,left = False,bottom = False)
axins.patch.set_alpha(0.6)
q = axins.arrow(0,0,0.05,0,color='black',head_length = 0.009)

moderate_shear_cf = ax2.contourf(imerg_cases['x'], imerg_cases['y'],weak_storm_and_moderate_shear_imerg.mean('case'),
                              levels=np.arange(0,7.1,0.5),cmap='jet')
ax2.grid()
ax2.set_title('IMERG Moderate-Shear (>= 10 kt and < 20 kt) \n n = ' + str(len(weak_storm_and_moderate_shear_imerg)))
ax2.set_xlabel('Along-Shear Direction (km)')

axins2 = inset_axes(ax2, width="25%", height="9%", loc=3, borderpad=0)
axins2.tick_params(labelleft=False, labelbottom=False,left = False,bottom = False)
axins2.patch.set_alpha(0.6)
q2 = axins2.arrow(0,0,0.05,0,color='black',head_length = 0.009)

strong_shear_cf = ax3.contourf(imerg_cases['x'], imerg_cases['y'],weak_storm_and_strong_shear_imerg.mean('case'),
                              levels=np.arange(0,7.1,0.5),cmap='jet')
ax3.grid()
ax3.set_title('IMERG Strong-Shear (>= 20 kt) \n n = ' + str(len(weak_storm_and_strong_shear_imerg)))
ax3.set_xlabel('Along-Shear Direction (km)')

axins3 = inset_axes(ax3, width="25%", height="9%", loc=3, borderpad=0)
axins3.tick_params(labelleft=False, labelbottom=False,left = False,bottom = False)
axins3.patch.set_alpha(0.6)
q3 = axins3.arrow(0,0,0.05,0,color='black',head_length = 0.009)

cax = plt.axes([0.105, 0, 0.8, 0.07])
# MAKE SURE COLOR LEVELS OF ALL PLOTS ARE SET EQUALLY!!!
plt.colorbar(strong_shear_cf,cax=cax,label='Precipitation (mm/h)',orientation='horizontal')

In [ ]:
current_env_info = pd.DataFrame(filtered_with_boo_multi_index.loc[multiple_conditions_index_finder([weak_storm_indices,
                                                       strong_shear_indices])].mean().round(2)).transpose()

current_env_info.index = ['Strong Shear']

current_env_info

In [ ]:
fig = plt.figure(figsize=(10, 5.5)) 

gs = fig.add_gridspec(1,2)
ax = fig.add_subplot(gs[0, 0],adjustable='box', aspect=1)
ax2 = fig.add_subplot(gs[0, 1],adjustable='box', aspect=1)

small_moderate_shear_diff_cf = ax.contourf(imerg_cases['x'], imerg_cases['y'],weak_storm_and_weak_shear_imerg.mean('case')-
                                           weak_storm_and_moderate_shear_imerg.mean('case'),
                              levels=np.arange(-4,4.1,0.5),cmap='bwr')
ax.grid()
ax.set_title('IMERG Weak-Shear – Moderate-Shear')
ax.set_xlabel('Along-Shear Direction (km)')
ax.set_ylabel('Across-Shear Direction (km)')

axins = inset_axes(ax, width="25%", height="9%", loc=3, borderpad=0)
axins.tick_params(labelleft=False, labelbottom=False,left = False,bottom = False)
axins.patch.set_alpha(0.6)
q = axins.arrow(0,0,0.05,0,color='black',head_length = 0.009)

moderate_shear_cf = ax2.contourf(imerg_cases['x'], imerg_cases['y'],weak_storm_and_weak_shear_imerg.mean('case')-
                                 weak_storm_and_strong_shear_imerg.mean('case'),
                              levels=np.arange(-4,4.1,0.5),cmap='bwr')
ax2.grid()
ax2.set_title('IMERG Weak-Shear – Strong-Shear')
ax2.set_xlabel('Along-Shear Direction (km)')

axins2 = inset_axes(ax2, width="25%", height="9%", loc=3, borderpad=0)
axins2.tick_params(labelleft=False, labelbottom=False,left = False,bottom = False)
axins2.patch.set_alpha(0.6)
q2 = axins2.arrow(0,0,0.05,0,color='black',head_length = 0.009)

cax = plt.axes([0.105, 0, 0.8, 0.07])
# MAKE SURE ALL COLOR LEVELS ARE SET EQUALLY!!!
plt.colorbar(moderate_shear_cf,cax=cax,label='Precipitation Difference (mm/h)',orientation='horizontal')
    


In [ ]:
weak_storm_weak_shear_RI_imerg = imerg_cases.sel(case=multiple_conditions_index_finder([weak_storm_indices,weak_shear_indices,RI_indices]))
weak_storm_moderate_shear_RI_imerg = imerg_cases.sel(case=multiple_conditions_index_finder([weak_storm_indices,moderate_shear_indices,
                                                                                            RI_indices]))
weak_storm_strong_shear_RI_imerg = imerg_cases.sel(case=multiple_conditions_index_finder([weak_storm_indices,strong_shear_indices,
                                                                                            RI_indices]))

fig = plt.figure(figsize=(20, 7)) 

gs = fig.add_gridspec(1,3)
ax = fig.add_subplot(gs[0, 0],adjustable='box', aspect=1)
ax2 = fig.add_subplot(gs[0, 1],adjustable='box', aspect=1)
ax3 = fig.add_subplot(gs[0, 2],adjustable='box', aspect=1)


weak_storm_weak_shear_RI_cf = ax.contourf(imerg_cases['x'], imerg_cases['y'],weak_storm_weak_shear_RI_imerg.mean('case'),
                              levels=np.arange(0,13.1,1),cmap='jet')
ax.grid()
ax.set_title('IMERG Weak-Shear (< 10 kt) RI \n n = ' + str(len(weak_storm_weak_shear_RI_imerg)))
ax.set_xlabel('Along-Shear Direction (km)')
ax.set_ylabel('Across-Shear Direction (km)')

axins = inset_axes(ax, width="25%", height="9%", loc=3, borderpad=0)
axins.tick_params(labelleft=False, labelbottom=False,left = False,bottom = False)
axins.patch.set_alpha(0.6)
q = axins.arrow(0,0,0.05,0,color='black',head_length = 0.009)

weak_storm_moderate_shear_RI_cf = ax2.contourf(imerg_cases['x'], imerg_cases['y'],weak_storm_moderate_shear_RI_imerg.mean('case'),
                              levels=np.arange(0,13.1,1),cmap='jet')
ax2.grid()
ax2.set_title('IMERG Moderate-Shear (>= 10 kt and < 20 kt) RI \n n = ' + str(len(weak_storm_moderate_shear_RI_imerg)))
ax2.set_xlabel('Along-Shear Direction (km)')

axins2 = inset_axes(ax2, width="25%", height="9%", loc=3, borderpad=0)
axins2.tick_params(labelleft=False, labelbottom=False,left = False,bottom = False)
axins2.patch.set_alpha(0.6)
q2 = axins2.arrow(0,0,0.05,0,color='black',head_length = 0.009)

weak_storm_strong_shear_RI_cf = ax3.contourf(imerg_cases['x'], imerg_cases['y'],weak_storm_strong_shear_RI_imerg.mean('case'),
                              levels=np.arange(0,13.1,1),cmap='jet')
ax3.grid()
ax3.set_title('IMERG Strong-Shear (>= 20 kt) RI \n n = ' + str(len(weak_storm_strong_shear_RI_imerg)))
ax3.set_xlabel('Along-Shear Direction (km)')

axins3 = inset_axes(ax3, width="25%", height="9%", loc=3, borderpad=0)
axins3.tick_params(labelleft=False, labelbottom=False,left = False,bottom = False)
axins3.patch.set_alpha(0.6)
q3 = axins3.arrow(0,0,0.05,0,color='black',head_length = 0.009)

cax = plt.axes([0.105, 0, 0.8, 0.07])
# MAKE SURE COLOR LEVELS OF ALL PLOTS ARE SET EQUALLY!!!
plt.colorbar(weak_storm_strong_shear_RI_cf,cax=cax,label='Precipitation (mm/h)',orientation='horizontal')

In [ ]:
weak_storm_strong_shear_RI_imerg

In [ ]:
fig = plt.figure(figsize=(20, 20)) 

gs = fig.add_gridspec(3,3)
ax = fig.add_subplot(gs[0, 0],adjustable='box', aspect=1)
ax2 = fig.add_subplot(gs[0, 1],adjustable='box', aspect=1)
ax3 = fig.add_subplot(gs[0, 2],adjustable='box', aspect=1)
ax4 = fig.add_subplot(gs[1, 0],adjustable='box', aspect=1)
ax5 = fig.add_subplot(gs[1, 1],adjustable='box', aspect=1)
ax6 = fig.add_subplot(gs[1, 2],adjustable='box', aspect=1)
ax7 = fig.add_subplot(gs[2, 0],adjustable='box', aspect=1)
ax8 = fig.add_subplot(gs[2, 1],adjustable='box', aspect=1)
ax9 = fig.add_subplot(gs[2, 2],adjustable='box', aspect=1)

comparison_mode = 'Weakening'

if comparison_mode == 'Slowly-Intensifying':
    Mode_indices = Slowly_intensifying_indices
elif comparison_mode == 'Steady-State':
    Mode_indices = SS_indices
elif comparison_mode == 'Weakening':
    Mode_indices = Weakening_indices
elif comparison_mode == 'Non-RI':
    Mode_indices = Non_RI_indices
    

weak_storm_weak_shear_mode_imerg = imerg_cases.sel(case=multiple_conditions_index_finder([weak_storm_indices,weak_shear_indices,
                                                                                            Mode_indices]))

weak_storm_moderate_shear_mode_imerg = imerg_cases.sel(case=multiple_conditions_index_finder([weak_storm_indices,moderate_shear_indices,
                                                                                            Mode_indices]))

weak_storm_strong_shear_mode_imerg = imerg_cases.sel(case=multiple_conditions_index_finder([weak_storm_indices,strong_shear_indices,
                                                                                            Mode_indices]))

weak_storm_weak_shear_mode_cf = ax.contourf(imerg_cases['x'], imerg_cases['y'],weak_storm_weak_shear_mode_imerg.mean('case'),
                              levels=np.arange(0,13.1,1),cmap='jet')
ax.grid()
ax.set_title('IMERG Weak-Shear (< 10 kt) ' + comparison_mode +'\n n = ' + str(len(weak_storm_weak_shear_mode_imerg)))
ax.set_ylabel('Across-Shear Direction (km)')

axins = inset_axes(ax, width="25%", height="9%", loc=3, borderpad=0)
axins.tick_params(labelleft=False, labelbottom=False,left = False,bottom = False)
axins.patch.set_alpha(0.6)
q = axins.arrow(0,0,0.05,0,color='black',head_length = 0.009)

weak_storm_moderate_shear_mode_cf = ax2.contourf(imerg_cases['x'], imerg_cases['y'],weak_storm_moderate_shear_mode_imerg.mean('case'),
                              levels=np.arange(0,13.1,1),cmap='jet')
ax2.grid()
ax2.set_title('IMERG Moderate-Shear (>= 10 kt and < 20 kt) ' +comparison_mode + '\n n = ' + str(len(weak_storm_moderate_shear_mode_imerg)))

axins2 = inset_axes(ax2, width="25%", height="9%", loc=3, borderpad=0)
axins2.tick_params(labelleft=False, labelbottom=False,left = False,bottom = False)
axins2.patch.set_alpha(0.6)
q2 = axins2.arrow(0,0,0.05,0,color='black',head_length = 0.009)

weak_storm_strong_shear_mode_cf = ax3.contourf(imerg_cases['x'], imerg_cases['y'],weak_storm_strong_shear_mode_imerg.mean('case'),
                              levels=np.arange(0,13.1,1),cmap='jet')
ax3.grid()
ax3.set_title('IMERG Strong-Shear (>= 20 kt) '+comparison_mode+'\n n = ' + str(len(weak_storm_strong_shear_mode_imerg)))

axins3 = inset_axes(ax3, width="25%", height="9%", loc=3, borderpad=0)
axins3.tick_params(labelleft=False, labelbottom=False,left = False,bottom = False)
axins3.patch.set_alpha(0.6)
q3 = axins3.arrow(0,0,0.05,0,color='black',head_length = 0.009)

weak_storm_weak_shear_RI_cf = ax4.contourf(imerg_cases['x'], imerg_cases['y'],weak_storm_weak_shear_RI_imerg.mean('case'),
                              levels=np.arange(0,13.1,1),cmap='jet')
ax4.grid()
ax4.set_title('IMERG Weak-Shear (< 10 kt) RI \n n = ' + str(len(weak_storm_weak_shear_RI_imerg)))
ax4.set_ylabel('Across-Shear Direction (km)')

axins4 = inset_axes(ax4, width="25%", height="9%", loc=3, borderpad=0)
axins4.tick_params(labelleft=False, labelbottom=False,left = False,bottom = False)
axins4.patch.set_alpha(0.6)
q4 = axins4.arrow(0,0,0.05,0,color='black',head_length = 0.009)

weak_storm_moderate_shear_RI_cf = ax5.contourf(imerg_cases['x'], imerg_cases['y'],weak_storm_moderate_shear_RI_imerg.mean('case'),
                              levels=np.arange(0,13.1,1),cmap='jet')
ax5.grid()
ax5.set_title('IMERG Moderate-Shear (>= 10 kt and < 20 kt) RI \n n = ' + str(len(weak_storm_moderate_shear_RI_imerg)))

axins5 = inset_axes(ax5, width="25%", height="9%", loc=3, borderpad=0)
axins5.tick_params(labelleft=False, labelbottom=False,left = False,bottom = False)
axins5.patch.set_alpha(0.6)
q5 = axins5.arrow(0,0,0.05,0,color='black',head_length = 0.009)

weak_storm_strong_shear_RI_cf = ax6.contourf(imerg_cases['x'], imerg_cases['y'],weak_storm_strong_shear_RI_imerg.mean('case'),
                              levels=np.arange(0,13.1,1),cmap='jet')
ax6.grid()
ax6.set_title('IMERG Strong-Shear (>= 20 kt) RI \n n = ' + str(len(weak_storm_strong_shear_RI_imerg)))

axins6 = inset_axes(ax6, width="25%", height="9%", loc=3, borderpad=0)
axins6.tick_params(labelleft=False, labelbottom=False,left = False,bottom = False)
axins6.patch.set_alpha(0.6)
q6 = axins6.arrow(0,0,0.05,0,color='black',head_length = 0.009)


weak_storm_weak_shear_diff_cf = ax7.contourf(imerg_cases['x'], imerg_cases['y'],weak_storm_weak_shear_RI_imerg.mean('case') - 
                                             weak_storm_weak_shear_mode_imerg.mean('case'),
                              levels=np.arange(-8,8.1,1),cmap='bwr')
ax7.grid()
ax7.set_title('IMERG Weak-Shear (< 10 kt) RI – ' + comparison_mode)
ax7.set_xlabel('Along-Shear Direction (km)')

axins7 = inset_axes(ax7, width="25%", height="9%", loc=3, borderpad=0)
axins7.tick_params(labelleft=False, labelbottom=False,left = False,bottom = False)
axins7.patch.set_alpha(0.6)
q7 = axins7.arrow(0,0,0.05,0,color='black',head_length = 0.009)

weak_storm_moderate_shear_diff_cf = ax8.contourf(imerg_cases['x'], imerg_cases['y'],weak_storm_moderate_shear_RI_imerg.mean('case')-
                                                 weak_storm_moderate_shear_mode_imerg.mean('case'),
                              levels=np.arange(-8,8.1,1),cmap='bwr')
ax8.grid()
ax8.set_title('IMERG Moderate-Shear (>= 10 kt and < 20 kt) RI – ' + comparison_mode)
ax8.set_xlabel('Along-Shear Direction (km)')

axins8 = inset_axes(ax8, width="25%", height="9%", loc=3, borderpad=0)
axins8.tick_params(labelleft=False, labelbottom=False,left = False,bottom = False)
axins8.patch.set_alpha(0.6)
q8 = axins8.arrow(0,0,0.05,0,color='black',head_length = 0.009)

weak_storm_strong_shear_diff_cf = ax9.contourf(imerg_cases['x'], imerg_cases['y'],weak_storm_strong_shear_RI_imerg.mean('case')-
                                               weak_storm_strong_shear_mode_imerg.mean('case'),
                              levels=np.arange(-8,8.1,1),cmap='bwr')
ax9.grid()
ax9.set_title('IMERG Strong-Shear (>= 20 kt) RI - ' + comparison_mode)

axins9 = inset_axes(ax9, width="25%", height="9%", loc=3, borderpad=0)
axins9.tick_params(labelleft=False, labelbottom=False,left = False,bottom = False)
axins9.patch.set_alpha(0.6)
q9 = axins9.arrow(0,0,0.05,0,color='black',head_length = 0.009)

cax = plt.axes([0.91, 0.375, 0.02, 0.52])
plt.colorbar(weak_storm_strong_shear_mode_cf,label='Precipitation (mm/h)',cax=cax)

cax_diff = plt.axes([0.91, 0.11, 0.02, 0.23])
plt.colorbar(weak_storm_strong_shear_diff_cf,label='Precipitation Difference (mm/h)',cax=cax_diff)


In [ ]:
current_env_info = pd.DataFrame(filtered_with_boo_multi_index.loc[multiple_conditions_index_finder([weak_storm_indices,strong_shear_indices,
                                                                                            RI_indices])].mean().round(2)).transpose()

current_env_info.index = ['Strong-Shear; RI']

current_env_info